# Set up imports

In [1]:
# setting up our imports
import re, string, unicodedata
import numpy as np
import pandas as pd
from pprint import pprint
import nltk
from nltk.corpus import stopwords
nltk.download('stopwords')
stop_words = stopwords.words('english')

# Gensim
import gensim
import gensim.corpora as corpora
from gensim.utils import simple_preprocess
from gensim.models import CoherenceModel
from gensim.models import LdaModel, LdaMulticore
import gensim.downloader as api
from gensim.models import LsiModel
from gensim.models import ldaseqmodel
from gensim.corpora import Dictionary, bleicorpus
from gensim.matutils import hellinger

nltk.download('wordnet')
from nltk.stem.porter import PorterStemmer
from nltk.stem.wordnet import WordNetLemmatizer
#from bs4 import BeautifulSoup
#from nltk import word_tokenize, sent_tokenize

# Plotting tools 
import pyLDAvis
import pyLDAvis.gensim  # don't skip this
import matplotlib.pyplot as plt
# %matplotlib inline

# Enable logging for gensim - optional
#import logging
#logging.basicConfig(format='%(asctime)s : %(levelname)s : %(message)s', level=logging.ERROR)
#logging.root.setLevel(level=logging.INFO)
#import warnings
#warnings.filterwarnings("ignore",category=DeprecationWarning)

[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\Kornelius\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\utils.py:1197: UserWarning: detected Windows; aliasing chunkize to chunkize_serial
  warnings.warn("detected Windows; aliasing chunkize to chunkize_serial")
[nltk_data] Downloading package wordnet to
[nltk_data]     C:\Users\Kornelius\AppData\Roaming\nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


# load dataset

In [2]:
# Load dataset
df = pd.read_csv('C:/Users/Kornelius/Desktop/Data 2/nips-papers/papers.csv', header = 0, sep = ';', error_bad_lines=False)
# Drop the columns not needed
df = df.drop(columns=['id', 'event_type', 'pdf_name'], axis=1)

In [3]:
# Drop a row by condition
df = df[df.abstract != 'Abstract Missing']

In [4]:
# sort by year
df = df.sort_values(by=['year'])
df

year                                              title  \
6389  1997        A Neural Network Based Head Tracking System   
5909  1997  Learning Generative Models with the Up Propaga...   
4884  2000   Algorithms for Non-negative Matrix Factorization   
5281  2001  Characterizing Neural Gain Control using Spike...   
4471  2007  Learning Horizontal Connections in a Sparse Co...   
4477  2007                 Predictive Matrix-Variate t Models   
4480  2007                        Competition Adds Complexity   
6095  2007  Progressive mixture rules are deviation subopt...   
6085  2007  Adaptive Embedded Subgraph Algorithms using Wa...   
3564  2007  Estimating disparity with confidence from ener...   
3430  2007          Discriminative Batch Mode Active Learning   
6000  2007   Random Sampling of States in Dynamic Programming   
4515  2007        Mining Internet-Scale Software Repositories   
3434  2007                Computing Robust Counter-Strategies   
5958  2007           The Infinite Gamma-Poisson Feature Model   
4607  2007  Linear programming analysis of loopy belief pr...   
6031  2007  Fitted Q-iteration in continuous action-space ...   
6202  2007  Efficient Convex Relaxation for Transductive S...   
4439  2007  An online Hebbian learning rule that performs ...   
4385  2007  On Ranking in Survival Analysis: Bounds on the...   
6255  2007  The Noisy-Logical Distribution and its Applica...   
4363  2007  Support Vector Machine Classification with Ind...   
3565  2007  Modelling motion primitives and their timing i...   
6271  2007  Modeling image patches with a directed hierarc...   
4276  2007  Gaussian Process Models for Link Analysis and ...   
4226  2007                Spatial Latent Dirichlet Allocation   
6405  2007  Regulator Discovery from Gene Expression Time ...   
6479  2007                            Supervised Topic Models   
3578  2007  EEG-Based Brain-Computer Interaction: Improved...   
6549  2007  A General Boosting Method and its Application ...   
...    ...                                                ...   
5371  2017         Independence clustering (without a matrix)   
5370  2017  Interpretable and Globally Optimal Prediction ...   
5383  2017  From Parity to Preference-based Notions of Fai...   
5368  2017  On Tensor Train Rank Minimization : Statistica...   
5358  2017  Gradients of Generative Models for Improved Di...   
5357  2017  Dual-Agent GANs for Photorealistic and Identit...   
5351  2017  Query Complexity of Clustering with Side Infor...   
3484  2017                       Welfare Guarantees from Data   
5337  2017  Subset Selection and Summarization in Sequenti...   
5327  2017  Clustering Billions of Reads for DNA Data Storage   
5360  2017  Expectation Propagation with Stochastic Kineti...   
5521  2017     Model evidence from nonequilibrium simulations   
5401  2017                Collecting Telemetry Data Privately   
5421  2017  Learning Combinatorial Optimization Algorithms...   
5506  2017  k-Support and Ordered Weighted Sparsity for Ov...   
5501  2017     From Bayesian Sparsity to Gated Recurrent Nets   
5498  2017  Minimax Estimation of Bandable Precision Matrices   
5492  2017  Lower bounds on the robustness to adversarial ...   
5488  2017  Union of Intersections (UoI) for Interpretable...   
5484  2017  Uprooting and Rerooting Higher-Order Graphical...   
5411  2017  When Cyclic Coordinate Descent Outperforms Ran...   
5465  2017  InfoGAIL: Interpretable Imitation Learning fro...   
5450  2017  The Expressive Power of Neural Networks: A Vie...   
5446  2017       Improving the Expected Improvement Algorithm   
5444  2017  Clustering Stable Instances of Euclidean k-means.   
5440  2017  Deliberation Networks: Sequence Generation Bey...   
5436  2017  On the Model Shrinkage Effect of Gamma Process...   
5434  2017      Regret Analysis for Continuous Dueling Bandit   
5459  2017  Identification of Gaussian Process State Space...   
5278  2017                    Hierarchica

In [5]:
df.year.value_counts()

2017    679
2016    569
2014    411
2015    403
2013    360
2012    342
2011    290
2010    288
2009    257
2008    222
2007     99
1997      2
2001      1
2000      1
Name: year, dtype: int64

In [6]:
data = df.abstract.values.tolist()

In [7]:
from nltk.corpus import stopwords 
from nltk.stem.wordnet import WordNetLemmatizer
import string
stop = set(stopwords.words('english'))
exclude = set(string.punctuation) 
ps = PorterStemmer()
def clean(data):
    stop_free = " ".join([i for i in data.lower().split() if i not in stop])
    punc_free = ''.join(ch for ch in stop_free if ch not in exclude)
    normalized = " ".join(ps.stem(word) for word in punc_free.split())
    return normalized

data = [clean(data).split() for data in data]  

In [8]:
# remove characters and numbers
def sent_to_words(sentences):
    for sentence in sentences:
        yield(gensim.utils.simple_preprocess(str(sentence), deacc=True))  # deacc=True removes punctuations

data_words = list(sent_to_words(data))

In [9]:
data = data_words
# Create Dictionary
id2word = corpora.Dictionary(data)
print((id2word))

Dictionary(12827 unique tokens: ['adapt', 'adjust', 'allow', 'also', 'auxiliari']...)


In [10]:
# Create Corpus
texts = data
# Term Document Frequency and creating corpus
corpus = [id2word.doc2bow(text) for text in texts]

In [11]:
from gensim.models import ldaseqmodel
import numpy
from gensim.matutils import hellinger

In [12]:
time_slice = [2 , 1, 1, 99, 222, 257, 288, 290, 342, 360, 411, 403, 569, 679]

In [13]:
#ldaseq = ldaseqmodel.LdaSeqModel(corpus=corpus, id2word=id2word, time_slice=time_slice, num_topics=5)

ldaseq = ldaseqmodel.LdaSeqModel(corpus=corpus , id2word=id2word , num_topics=10, time_slice=time_slice)

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

...

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldaseqmodel.py:230: RuntimeWarning: divide by zero encountered in double_scalars
  convergence = np.fabs((bound - old_bound) / old_bound)


In [14]:
#ldaseq.print_topics(time=0) # at timeslice 1, those are the topics, word probability to the right 

In [15]:
ldaseq.print_topic_times(topic=0) # evolution of 1st topic through all timeslices

[[('problem', 0.03787553579054866),
  ('algorithm', 0.031065254342854697),
  ('function', 0.021547116167934307),
  ('optim', 0.021237173264665496),
  ('method', 0.017966120193285102),
  ('convex', 0.012829856336618645),
  ('solut', 0.011115138609399838),
  ('converg', 0.010576220556544929),
  ('solv', 0.010183098004813842),
  ('regular', 0.010064847280737232),
  ('propos', 0.009597846720530228),
  ('approxim', 0.009106733402582808),
  ('show', 0.009101849843230448),
  ('program', 0.007900807783312602),
  ('result', 0.00781714117104154),
  ('linear', 0.0076345131391686765),
  ('use', 0.007562619456683949),
  ('minim', 0.007452929613680258),
  ('paper', 0.0071068863113959505),
  ('learn', 0.006852309863645776)],
 [('problem', 0.03798619232480421),
  ('algorithm', 0.03114887530475918),
  ('function', 0.02159878397591492),
  ('optim', 0.021286969231253308),
  ('method', 0.018004762802903095),
  ('convex', 0.01285404567757748),
  ('solut', 0.011133824890052097),
  ('converg', 0.010593759040

In [16]:
ldaseq.print_topic_times(topic=1) 

[[('model', 0.028756409216767136),
  ('distribut', 0.019709667286714857),
  ('use', 0.017256258202060473),
  ('data', 0.01637427981808062),
  ('infer', 0.014221239336605292),
  ('method', 0.013961485288417095),
  ('estim', 0.013839805691169492),
  ('process', 0.012928285291318339),
  ('bayesian', 0.011260297164453644),
  ('approach', 0.01030213154207163),
  ('kernel', 0.009341791230028502),
  ('sampl', 0.008673956403967654),
  ('propos', 0.008093769561382561),
  ('approxim', 0.007773885397286875),
  ('comput', 0.007344421408608617),
  ('gener', 0.00729537544582674),
  ('learn', 0.007294914447873163),
  ('gaussian', 0.00665627528423823),
  ('base', 0.006636646508513385),
  ('effici', 0.006263604429030604)],
 [('model', 0.028840576411731628),
  ('distribut', 0.019759484084354097),
  ('use', 0.017294441752494727),
  ('data', 0.016412974295033158),
  ('infer', 0.01425271698482431),
  ('method', 0.013991958953041301),
  ('estim', 0.013868929927625945),
  ('process', 0.0129542932363424),
  (

In [17]:
ldaseq.print_topic_times(topic=2) 

[[('model', 0.020992575862064947),
  ('neuron', 0.01597882255728191),
  ('neural', 0.014877677324793491),
  ('spike', 0.012494822172004675),
  ('activ', 0.01216058362328563),
  ('dynam', 0.011389858507951984),
  ('respons', 0.010405834266770225),
  ('system', 0.009015233247919759),
  ('brain', 0.008990284103846832),
  ('function', 0.008400722919301166),
  ('signal', 0.007823442919208624),
  ('use', 0.007446193068398525),
  ('network', 0.00734361696037175),
  ('time', 0.007259004188805209),
  ('inform', 0.00708969862515003),
  ('process', 0.0067692034263718915),
  ('popul', 0.006354492774880239),
  ('show', 0.005982293604632625),
  ('connect', 0.005959824965981103),
  ('state', 0.005956658539952175)],
 [('model', 0.021037881155922224),
  ('neuron', 0.01606697615907089),
  ('neural', 0.014758524976193862),
  ('spike', 0.012553166337925574),
  ('activ', 0.012216506342956861),
  ('dynam', 0.01143941396037198),
  ('respons', 0.010447876292768882),
  ('brain', 0.009023108228265998),
  ('syst

In [18]:
ldaseq.print_topic_times(topic=3) 

[[('cluster', 0.03476836390811397),
  ('graph', 0.02362061093739526),
  ('data', 0.01846207886039038),
  ('structur', 0.016541532658884136),
  ('tree', 0.013933006478239206),
  ('algorithm', 0.012756438285337318),
  ('set', 0.009490145361291533),
  ('model', 0.009127290961879756),
  ('problem', 0.008432810911014913),
  ('node', 0.008373740188522528),
  ('use', 0.0083587964137234),
  ('propos', 0.0076323803386826525),
  ('detect', 0.007471945352338667),
  ('predict', 0.006847028890235149),
  ('network', 0.006664286728359087),
  ('relat', 0.006448888749886522),
  ('group', 0.006126611112761698),
  ('user', 0.006023158117236721),
  ('comput', 0.005807158777625663),
  ('partit', 0.005757298905002059)],
 [('cluster', 0.0348742269564204),
  ('graph', 0.023682886780458965),
  ('data', 0.018504999359074965),
  ('structur', 0.01657949117502371),
  ('tree', 0.013962759132983813),
  ('algorithm', 0.012781780023444952),
  ('set', 0.009506103793360985),
  ('model', 0.009141974842930285),
  ('proble

In [19]:
ldaseq.print_topic_times(topic=4) 

[[('model', 0.03439301785822065),
  ('imag', 0.02863318497247055),
  ('learn', 0.018372045204862072),
  ('object', 0.014875221256082021),
  ('use', 0.014520939791982858),
  ('task', 0.012199236536690904),
  ('human', 0.010948001983104078),
  ('featur', 0.009708019699943705),
  ('visual', 0.008440262607148577),
  ('approach', 0.007596421380028735),
  ('represent', 0.007114556487504847),
  ('gener', 0.006774194381798062),
  ('recognit', 0.006654008011510086),
  ('train', 0.006518937683134786),
  ('propos', 0.006132405214528405),
  ('show', 0.0056501711754219745),
  ('result', 0.00560014712832719),
  ('two', 0.0054536472383566285),
  ('perform', 0.005306674657245781),
  ('scene', 0.004955401860548719)],
 [('model', 0.03457154282259385),
  ('imag', 0.028506994971442955),
  ('learn', 0.01835188903631768),
  ('object', 0.014893109813288261),
  ('use', 0.01446794570311748),
  ('task', 0.012263143458335884),
  ('human', 0.011001208526965546),
  ('featur', 0.009751448715100105),
  ('visual', 0.

In [20]:
ldaseq.print_topic_times(topic=5) 

[[('learn', 0.036751994889098756),
  ('data', 0.023517191710373378),
  ('method', 0.01819539791192419),
  ('featur', 0.016919047478085036),
  ('use', 0.014329985649033008),
  ('label', 0.013347013124899814),
  ('classif', 0.013320554649506421),
  ('classifi', 0.010855763780818838),
  ('kernel', 0.01065979878324107),
  ('train', 0.010659197302358562),
  ('approach', 0.009886249567566978),
  ('perform', 0.009822719520281496),
  ('set', 0.009413456846908305),
  ('show', 0.009054859486562927),
  ('task', 0.008471819312998851),
  ('propos', 0.007879165805544711),
  ('algorithm', 0.007607857844458104),
  ('result', 0.007551875998579183),
  ('function', 0.00673158521097485),
  ('error', 0.006348725629749699)],
 [('learn', 0.03675447430046132),
  ('data', 0.023592119736817876),
  ('method', 0.018249166599237063),
  ('featur', 0.016965165630012293),
  ('use', 0.014343794423675078),
  ('label', 0.013378059716099159),
  ('classif', 0.013351820015241303),
  ('classifi', 0.010877950721213883),
  ('

In [21]:
ldaseq.print_topic_times(topic=6) 

[[('network', 0.03324906693525955),
  ('gradient', 0.014735287793020817),
  ('comput', 0.014650961125434455),
  ('learn', 0.014443102401617312),
  ('method', 0.013127901885583085),
  ('use', 0.012481437716013063),
  ('train', 0.012478250334545632),
  ('memori', 0.011785018735791157),
  ('algorithm', 0.010874623616152632),
  ('perform', 0.009786544509667523),
  ('stochast', 0.00956902282681523),
  ('deep', 0.009084723396355666),
  ('neural', 0.008527185181066758),
  ('time', 0.007840264367420998),
  ('weight', 0.007131146980059894),
  ('layer', 0.006895713596048878),
  ('larg', 0.006829777677256339),
  ('show', 0.00639038304125365),
  ('improv', 0.006126339189580889),
  ('propos', 0.005941058828394936)],
 [('network', 0.03313214307739067),
  ('gradient', 0.014789054643764996),
  ('comput', 0.014704060030634436),
  ('learn', 0.014476695396175725),
  ('method', 0.013171847615117247),
  ('use', 0.012494734781741547),
  ('train', 0.012466602831264006),
  ('memori', 0.011822469294604817),
  

In [22]:
ldaseq.print_topic_times(topic=7) 

[[('algorithm', 0.03407893505558776),
  ('learn', 0.0227685611024624),
  ('problem', 0.012315716645627195),
  ('polici', 0.011129803308472349),
  ('bound', 0.010790754918549484),
  ('onlin', 0.010192314100632958),
  ('set', 0.009907445801199294),
  ('optim', 0.00880024375331636),
  ('show', 0.00845698095907753),
  ('gener', 0.007273975996553429),
  ('result', 0.007182869808973114),
  ('function', 0.007098592449234432),
  ('regret', 0.007013343337725072),
  ('decis', 0.00658407753319498),
  ('use', 0.006573467835802875),
  ('action', 0.006063500211239589),
  ('time', 0.005369804057596839),
  ('state', 0.005155606396292423),
  ('reward', 0.005106061670332597),
  ('loss', 0.005017153561442877)],
 [('algorithm', 0.03419082069227262),
  ('learn', 0.022834447109260435),
  ('problem', 0.012342889073311197),
  ('polici', 0.011153692085159893),
  ('bound', 0.010813022496204182),
  ('onlin', 0.010213303199315836),
  ('set', 0.009927632603966813),
  ('optim', 0.008817060400029034),
  ('show', 0.0

In [23]:
ldaseq.print_topic_times(topic=8)

[[('model', 0.035034561344247886),
  ('data', 0.01563191347307925),
  ('matrix', 0.015190178359427261),
  ('method', 0.014167227213631615),
  ('spars', 0.014122132489908436),
  ('latent', 0.013784445000173243),
  ('use', 0.011302207197521336),
  ('algorithm', 0.011064696471231083),
  ('rank', 0.01076084216219009),
  ('structur', 0.010342140451975769),
  ('propos', 0.009997524126354978),
  ('variabl', 0.008896345645216113),
  ('problem', 0.008715925484267131),
  ('topic', 0.008164916576044637),
  ('approach', 0.007304238372042063),
  ('factor', 0.0069497383937769715),
  ('document', 0.006623703145502449),
  ('show', 0.006328162580659084),
  ('learn', 0.006201893246653579),
  ('observ', 0.006072383398237988)],
 [('model', 0.035083066680899534),
  ('data', 0.015673565467957028),
  ('matrix', 0.015230127719868322),
  ('method', 0.01420133479842019),
  ('spars', 0.014158586000041964),
  ('latent', 0.013819254032891887),
  ('use', 0.01131467115209807),
  ('algorithm', 0.011062626005048155),


In [24]:
ldaseq.print_topic_times(topic=9) 

[[('estim', 0.024980785464920403),
  ('bound', 0.02152828818598214),
  ('algorithm', 0.01407935368236284),
  ('random', 0.01278077380024606),
  ('sampl', 0.011849238525616363),
  ('show', 0.011160935923856268),
  ('model', 0.010149820587728784),
  ('condit', 0.009671963975725749),
  ('distribut', 0.008814906031098212),
  ('provid', 0.008801672296184187),
  ('result', 0.007787190854333248),
  ('rate', 0.007463628792340199),
  ('gener', 0.00724633530333645),
  ('error', 0.006979460148583297),
  ('use', 0.00662906983495901),
  ('complex', 0.00650127964179228),
  ('converg', 0.006279063225168569),
  ('comput', 0.006225448409849083),
  ('probabl', 0.0058989671769248105),
  ('paramet', 0.0057379992006957965)],
 [('estim', 0.025080545102018095),
  ('bound', 0.021607678859984762),
  ('algorithm', 0.014045596064347627),
  ('random', 0.012816647558711577),
  ('sampl', 0.011881054620714262),
  ('show', 0.011189643999408654),
  ('model', 0.010160418544192987),
  ('condit', 0.009694690764997653),
 

In [25]:
    # to check Document - Topic proportions, use `doc-topics`
#doc = ldaseq.doc_topics(558) # check the 558th document in the corpuses topic distribution
#print (doc)
# this document is made up of different topics like this

In [26]:
# make a graph by checking the topic proportions and putting them on a graph 
# same with coherence
# do hellingers distance between topics?

In [27]:
ldaseq.print_topic_times(1) # evolution of 2nd topic through all timeslices


[[('model', 0.028756409216767136),
  ('distribut', 0.019709667286714857),
  ('use', 0.017256258202060473),
  ('data', 0.01637427981808062),
  ('infer', 0.014221239336605292),
  ('method', 0.013961485288417095),
  ('estim', 0.013839805691169492),
  ('process', 0.012928285291318339),
  ('bayesian', 0.011260297164453644),
  ('approach', 0.01030213154207163),
  ('kernel', 0.009341791230028502),
  ('sampl', 0.008673956403967654),
  ('propos', 0.008093769561382561),
  ('approxim', 0.007773885397286875),
  ('comput', 0.007344421408608617),
  ('gener', 0.00729537544582674),
  ('learn', 0.007294914447873163),
  ('gaussian', 0.00665627528423823),
  ('base', 0.006636646508513385),
  ('effici', 0.006263604429030604)],
 [('model', 0.028840576411731628),
  ('distribut', 0.019759484084354097),
  ('use', 0.017294441752494727),
  ('data', 0.016412974295033158),
  ('infer', 0.01425271698482431),
  ('method', 0.013991958953041301),
  ('estim', 0.013868929927625945),
  ('process', 0.0129542932363424),
  (

In [28]:
from gensim.models.coherencemodel import CoherenceModel

# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=2)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass1", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV1", cm_DTM.get_coherence())



# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=3)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass2", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV2", cm_DTM.get_coherence())



# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=4)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass3", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV3", cm_DTM.get_coherence())




# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=5)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass4", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV4", cm_DTM.get_coherence())



# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=6)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass5", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV5", cm_DTM.get_coherence())



# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=7)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass6", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV6", cm_DTM.get_coherence())



# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=8)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass7", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV7", cm_DTM.get_coherence())



# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=9)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass8", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV8", cm_DTM.get_coherence())



# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=10)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass9", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV9", cm_DTM.get_coherence())




# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=11)
# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass10", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV10", cm_DTM.get_coherence())


# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=12)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass11", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV11", cm_DTM.get_coherence())



# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=13)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass12", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV12", cm_DTM.get_coherence())

U_Mass1 -1.5805338389738117
CV1 0.3740562537354678
U_Mass2 -1.580511905975706
CV2 0.3740562537354678
U_Mass3 -1.5704527711299345
CV3 0.37116174734265345
U_Mass4 -1.57401406468081
CV4 0.37464863873805776
U_Mass5 -1.541152674958468
CV5 0.3721096975652777
U_Mass6 -1.5223650190854205
CV6 0.3707496653486233
U_Mass7 -1.5668771567508994
CV7 0.3754244889240669
U_Mass8 -1.5573827700600755
CV8 0.3800393793055889
U_Mass9 -1.6003830342707857
CV9 0.38502654556267835
U_Mass10 -1.5985014280746757
CV10 0.390443366406019
U_Mass11 -1.6216454321910827
CV11 0.3978024818163333
U_Mass12 -1.655068909904474
CV12 0.3981580595801639


In [29]:
#graph coherence and topic distribution per time slice

In [30]:
#https://datascience.blog.wzb.eu/2017/11/09/topic-modeling-evaluation-in-python-with-tmtoolkit/